# Solving the Set Packing Problem

In this notebook, we will describe how to solve the **Set Packing** problem with LunaSolve. We will begin by defining, explaining and giving an example for the Set Packing problem. We will then continue by modeling a problem instance, optimize it and implement the solution using LunaSolve. Finally, we will also take a further look at the interpretation of the answer we are returned from Luna.


## Table of Contents

1. [Introduction](#1)
2. [Real World Example](#2)
3. [Solving the Set Packing problem with Luna](#3)



<a id="1"></a>
## 1. Introduction

## **Set Packing problem** 

The Set Packing problem is a fundamental problem in combinatorial optimization and computer science. A problem set is given which is made up of subsets from a universal set containing some elements. The problem involves finding the maximal number of subsets in which all subsets have as an intersection equal to the empty set. This problem has widespread applications in areas such as resource allocation, scheduling, network design, and information retrieval. 

Formally, a universal set $U = \{e_1, e_2, \ldots, e_n\}$ and the family of subsets of $U$, $\mathcal{S} = \{S_1, S_2, \dots, S_m\}$ is defined, where each subset $(S_j \subseteq U)$ is associated with a cost $(c_j \ge 0)$. The Set Packing problem seeks to find a sub-collection $\mathcal{S}^* \subseteq \mathcal{S}$ such that:

1. **No Overlap**: 
$$
\forall\, S_i, S_j \in \mathcal{S}^* \text{ with } i \neq j,\quad S_i \cap S_j = \emptyset.
$$

2. **Optimality**:
$$
\max_{\mathcal{S}^* \subseteq \mathcal{S}} \sum_{S_i \in \mathcal{S}^*} w_i.
$$

This means we want to include as many subsets (based on their cost) while not including any elements from the universal set more than once. Importantly it is not necessary that we include every element from the universal set, only that each does not appear more than once. 


<a id="2"></a>
## 2. Description

Imagine you are managing a community center that offers various workshops to its members. Each workshop requires specific instructors, and each instructor can only teach one workshop at a time. During every hour of the day, lectures will be taking place simultaneously. Your goal is to schedule as many workshops as possible at each hour without any instructor being double-booked. This scenario encapsulates the essence of the Set Packing problem by trying to: select the maximum number of mutually disjoint subsets (workshops which need instructors) while trying to not double allocate instructors (from the universal set).

An instance of the example might be as follows. At your community center, there will be a total of 5 instructors available (the universal set) which are needed in different combinations at 7 different workshops. Your task will be to select the largest subset of workshops where there are no staff conflicts between the workshops.

universal_set = {Instructor A,Instructor B,Instructor C,Instructor D,Instructor E}

workshop_set = {W1 :{Instructor A,Instructor B}, W2:{Instructor B,Instructor C}, W3 :{Instructor C,Instructor D}, W4 :{Instructor D,Instructor E}, W5 :{Instructor A,Instructor E}, W6 :{Instructor B,Instructor D}, W7 :{Instructor C,Instructor E}}

- Workshop W1 requires instructor A and instructor B.  
- Workshop W2 requires instructor B and instructor C.  
- Workshop W3 requires instructor C and instructor D.  
- Workshop W4 requires instructor D and instructor E.  
- Workshop W5 requires instructor A and instructor E.  
- Workshop W6 requires instructor B and instructor D.  
- Workshop W7 requires instructor C and instructor E.

A trivial cost we could give to each workshop might be that of 1, where each is valued equally. However, we can also associate the expected number of interested visitors we expect for each workshop. Thereby aiming to maximize also the capacity for expected visitors.

<a id="3"></a>
## 3. Solving the Set Packing problem with Luna

To follow along with the next steps we need to install the **luna-quantum**  package for encoding and solving our optimization problem. 

The cell below installs the package for you if it is not already installed.

In [1]:
# Install dependencies
%pip install --upgrade pip
%pip install luna-quantum --upgrade

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


### 3.1 Set up Luna Client
Now, let's walk through the implementation of the Minimum Vertex Cover problem using LunaSolve. First, create an encryption key. You can generate a key [here](https://docs.aqarios.com/get-started#luna-encryption).

In [2]:
import os
os.environ["LUNA_ENCRYPTION_KEY"] = "gzaUL8hDECWXRcGrJiEa5wVWVgt4sgPbBDjKN8I92ps"

As the next step, instantiate a LunaSolve object and set your credentials. The API key is needed to identify you and grant access to the Luna platform. You can find it in your Aqarios account settings.

In [3]:
from luna_sdk import LunaSolve
ls = LunaSolve(api_key="60360df4e8b54305aababfa6ac99429e")

### 3.2 Create a Set Packing problem

To create a Set Packing instance we must encode our problem into a subset matrix of size (m x n), with m being the number of subsets and n the number of elements in the universal set. The subset matrix is made up of rows representing each subset. The $j_{th}$ value is 1 if element $j$ of the universal set is included in the subset represented by the row.

We can encode this matrix ourselves or alternatively use the `SetCover.gen_subsets_matrix([1, 2, 3], [[1, 2], [2, 3], [3]])` method, where a list containing the universal set and a list containing all subsets as lists, must be provided as arguments.

Below we will create the universal and lecture sets, and create a subset matrix using the `gen_subsets_matrix()` method. However, the subset matrix is also explicitly written out for an easier understanding.

Additionally the weights of each subset are given as a list containing $m$ costs, one for each subset.

In [4]:
universal_set = {
    "Instructor A",
    "Instructor B",
    "Instructor C",
    "Instructor D",
    "Instructor E"
}

workshops = {
    "W1": {"Instructor A", "Instructor B"}, #p j
    "W2": {"Instructor B", "Instructor C"},
    "W3": {"Instructor C", "Instructor D"}, #j
    "W4": {"Instructor D", "Instructor E"}, #p
    "W5": {"Instructor A", "Instructor E"},
    "W6": {"Instructor B", "Instructor D"}, #p j
    "W7": {"Instructor C", "Instructor E"} #p j
}


subset_matrix = [[1, 1, 0, 0, 0],
 [0, 1, 1, 0, 0],
 [0, 0, 1, 1, 0],
 [0, 0, 0, 1, 1],
 [1, 0, 0, 0, 1],
 [0, 1, 0, 1, 0],
 [0, 0, 1, 0, 1]]

subset_weights = [1, 1, 1, 1, 1, 1, 1]


### 3.3 Creating a Set Packing Object
To find the largest packing of our subsets using LunaSolve, we define the Set Packing use case using Luna’s `SetPacking` class. This class converts the subset matrix and the costs into a QUBO optimization problem, which Luna can then optimize.

In [5]:
# import the Set Packing object from the luna sdk
from luna_sdk.schemas import SetPacking

# create a Set Packing object
set_packing = SetPacking(subset_matrix=subset_matrix, weights=subset_weights, P=10000)



### 3.4 Create a Luna Optimization

We can now upload the problem instance as an optimization to Luna and solve it afterwards.

In [6]:
optimization = ls.optimization.create_from_use_case(name="Set Packing", use_case=set_packing)


### 3.5 Create a Luna job

The next step involves creating a job, which is an outbound request to the hardware provider to solve the optimisation problem. By calling the `ls.solution.create()` method of LunaSolve we can create the outbound job. This method takes care of optimizing our problem. To solve the Set Packing problem, we pass the `optimization_id` from our optimisation object of our use case, specify the `solver_name` we choose, the `provider` of the computing hardware, `solver_parameters` (which may be specific to the solver), and a `qpu_token` if needed.

In this instance, we solve the Set Packing problem using simulated annealing (sa) and choose D-Wave (dwave) as the hardware provider.

In [7]:
job = ls.solution.create(
    optimization_id=optimization.id,
    solver_name="sa",
    provider="dwave",
    solver_parameters={}
)

### 3.6 Retrieve the Solution

In step 3.4, we uploaded the problem, and in 3.5, we made a solve request to Luna. Luna sends the optimisation problem to the provider specified and is returned a solution. Luna autonomously takes care of all background activities, during which the user can turn to other of their important matters. The background processes include the creation and translation of the optimisation problem for the according hardware provider, sending out the request and obtaining a result back, and translating the solution back to an interpretable format.

The `Solution` object created, has multiple attributes expressing different factors of the optimisation problem. These include meta data of the optimisation and the sampled results. The optimisation meta data includes information attached to the use case problem, such as `id`, `name`, `solver`and `provider` names, `runtime` and `qpu` type. Lastly, the `status` variable indicates if the job has been successfully executed and returned to Luna. If the status variable says DONE, the optimisation has finished. In the case REQUESTED is displayed for the status, your optimisation is still being processed. Wait a little bit and re-execute the cell, to retrieve the updated solution.

In [8]:
solution = ls.solution.get(solution_id=job.id)
print(solution)

id: 67b5f03dacb6eea462be3a70
name: None
status: REQUESTED
solver: SA
provider: dwave
runtime: None
optimization_name: QUBO_MATRIX
created_date: 2025-02-19 14:52:45 (+07)
results:
    No results..
    Solution has status: REQUESTED



Because we converted the use case into the QUBO format, the solution we are returned from our provider is also in this format, which typically is in a vectorised form. However, the encoding from our original optimisation problem might be different. Slack variables, linearisations and other transformations can alter the variable description of optimisation methods. As aforementioned, Luna performs a post-processing step which transforms the solution from the QUBO domain back to a more intuitive domain. 

The `ls.solution.get_use_case_representation(solution_id=job.id)` method transforms the solution of our optimisation to a readable format. The `sense`attribute informs us if we are trying to maximize or minimize our objective function. The `result` is typically given as an iterable containing the `representation` which contains the solution, and the `òbj_value`. The objective value is difficult to interpret as it encompasses both optimization values and constraint penalties, however smaller values express better solutions. The `description` explains the encoding of the `representation` of the result. 

In the formal definition of the Set Packing problem, the variables $x_i$ represent the subsets $S_i$ from the family $S$ in the same order as given in our list. If the decision value of $x_i$ is equal to one, then the subset with index $i$ is part of the packing, while zero means that the subset is not part. The formulation additionally includes decision variables with two indices $ij$, which are support variables that ensure that each element from the universal set is represented not more than once in the packing (ensure the constraints). 

Accordingly, in the case of the Set Packing problem, the representation is a list which contains the indices of all subsets that have been selected to be included in the packing. In other words, the representation is a list of all indices $i$, for which their decision variable $x_i$ is equal to one. 


In [9]:
use_case_repr = ls.solution.get_use_case_representation(solution_id=job.id)
print(use_case_repr)

sense: min
results: [{'representation': [0, 2, 5, 6], 'obj_value': -4.0}]
description: The solution is a list containing the indices of subsets which are part of the packing.



Finally, if we wish to see the best solution from all evaluated samples we can call the `ls.solution.get_best_use_case_result(use_case_representation=use_case_repr)` method.

In [10]:
best_solution = ls.solution.get_best_use_case_result(use_case_representation=use_case_repr)
print(best_solution)

representation=[0, 2, 5, 6] obj_value=-4.0
